## Comparing feature maps between normal model and robust model
### Comapring adversarial images' feature maps

In [17]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
device = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=1, shuffle=False, num_workers=4)

robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=device) # original model
attack1 = PGD(robust_model, cuda=device) # robust model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.to(device)
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(pgd_imgs)
    
    robust_holder = []
    
    def forwardhooking(m, inp, out):
        robust_holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)
    
    robust_model(pgd_imgs)
    
    # for name, 
    
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], robust_holder[0][:,:,-1])
    _, max_indcies = torch.topk(sim, 1, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 1, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()

    max_list.extend(max_indcies)
    min_list.extend(min_indcies)
    

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


whole channel : 512

In [18]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

5 
 [(0, 8258), (1, 1535), (2, 185), (3, 14), (4, 8)]


In [19]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

510 
 [(37, 133), (54, 92), (220, 87), (3, 82), (61, 81), (110, 78), (130, 76), (189, 69), (139, 68), (101, 64), (14, 63), (176, 57), (58, 56), (248, 55), (250, 54), (237, 53), (21, 53), (165, 52), (102, 51), (505, 50), (124, 50), (84, 50), (92, 49), (164, 48), (87, 48), (25, 48), (178, 47), (96, 46), (138, 46), (293, 45), (94, 45), (229, 45), (32, 44), (192, 43), (494, 41), (214, 41), (9, 41), (0, 41), (466, 41), (1, 40), (26, 40), (468, 40), (112, 40), (224, 39), (40, 39), (402, 39), (47, 39), (419, 39), (18, 39), (271, 38), (270, 38), (255, 38), (476, 38), (29, 38), (117, 37), (215, 37), (415, 37), (51, 37), (457, 37), (417, 37), (45, 36), (228, 36), (46, 36), (95, 36), (86, 36), (134, 35), (42, 35), (109, 35), (77, 35), (203, 34), (49, 34), (249, 34), (114, 33), (372, 33), (182, 33), (108, 32), (287, 32), (137, 32), (212, 32), (62, 32), (57, 31), (116, 31), (197, 31), (129, 31), (151, 31), (445, 31), (91, 31), (389, 31), (497, 31), (128, 30), (390, 30), (247, 30), (342, 30), (68, 3

## Comparing original images' feature maps and adversarial images' feature maps
### 1. Original model

In [30]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(ori_imgs)
    model(pgd_imgs)
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    _, max_indcies = torch.topk(sim, 1, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 1, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()

    for i in range(batch_size):
        max_list.extend(max_indcies[i])
        min_list.extend(min_indcies[i])

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


In [31]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

58 
 [(0, 3335), (1, 2174), (2, 1419), (4, 469), (3, 461), (7, 359), (5, 355), (9, 324), (6, 323), (10, 145), (11, 102), (13, 64), (8, 58), (14, 54), (12, 50), (18, 46), (16, 28), (22, 25), (31, 24), (21, 21), (20, 21), (33, 19), (25, 17), (17, 12), (43, 11), (24, 10), (19, 9), (27, 7), (35, 6), (26, 6), (15, 6), (46, 4), (42, 4), (54, 3), (91, 2), (73, 2), (29, 2), (69, 2), (28, 2), (124, 1), (97, 1), (104, 1), (36, 1), (53, 1), (51, 1), (68, 1), (52, 1), (37, 1), (70, 1), (188, 1), (23, 1), (85, 1), (127, 1), (41, 1), (172, 1), (218, 1), (110, 1), (44, 1)]


In [32]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

503 
 [(4, 116), (0, 101), (1, 99), (2, 93), (3, 89), (5, 84), (17, 84), (14, 82), (21, 80), (10, 79), (23, 79), (11, 79), (13, 78), (25, 77), (12, 76), (29, 75), (34, 73), (16, 73), (15, 72), (24, 72), (28, 71), (32, 68), (19, 67), (7, 67), (55, 67), (27, 66), (18, 65), (6, 65), (30, 63), (26, 62), (56, 61), (8, 59), (40, 58), (58, 56), (46, 55), (48, 55), (82, 54), (9, 54), (20, 54), (71, 53), (33, 53), (36, 52), (79, 52), (69, 52), (39, 51), (37, 51), (59, 50), (62, 50), (74, 50), (51, 49), (100, 49), (52, 49), (44, 49), (85, 48), (88, 48), (47, 47), (67, 47), (50, 47), (57, 46), (101, 46), (35, 46), (38, 46), (41, 45), (60, 45), (65, 45), (77, 44), (87, 44), (107, 44), (90, 44), (63, 44), (72, 44), (42, 43), (68, 43), (118, 43), (70, 43), (53, 42), (98, 42), (133, 42), (99, 41), (96, 41), (92, 41), (103, 41), (112, 41), (94, 41), (84, 40), (66, 40), (73, 39), (83, 38), (111, 38), (89, 38), (64, 38), (119, 38), (95, 37), (22, 37), (49, 37), (78, 37), (45, 36), (104, 36), (31, 36), (

### 2. Robust model

In [36]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(cuda)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()


attack = PGD(robust_model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    robust_model(ori_imgs)
    robust_model(pgd_imgs)
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    _, max_indcies = torch.topk(sim, 1, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 1, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()

    for i in range(batch_size):
        max_list.extend(max_indcies[i])
        min_list.extend(min_indcies[i])

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


In [37]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

14 
 [(0, 5906), (1, 2796), (2, 836), (3, 290), (4, 72), (5, 44), (7, 16), (9, 14), (8, 12), (6, 4), (13, 4), (10, 3), (12, 2), (14, 1)]


In [38]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

503 
 [(3, 321), (6, 201), (12, 190), (15, 182), (20, 156), (5, 131), (4, 126), (18, 124), (14, 122), (2, 119), (24, 115), (43, 108), (55, 99), (0, 98), (8, 95), (9, 91), (7, 88), (19, 86), (30, 81), (11, 81), (35, 78), (29, 74), (50, 74), (78, 73), (16, 70), (21, 69), (84, 69), (97, 68), (62, 67), (13, 65), (10, 62), (68, 61), (56, 60), (28, 58), (117, 58), (87, 57), (48, 54), (17, 54), (92, 52), (26, 50), (248, 48), (113, 46), (185, 45), (1, 44), (51, 44), (133, 44), (34, 42), (247, 42), (89, 42), (23, 41), (42, 41), (255, 41), (116, 40), (154, 39), (164, 37), (98, 36), (96, 36), (355, 36), (221, 35), (138, 34), (46, 34), (220, 34), (123, 34), (150, 34), (93, 33), (115, 32), (49, 32), (38, 32), (44, 31), (336, 31), (400, 31), (86, 31), (94, 30), (196, 30), (210, 30), (468, 29), (182, 29), (64, 29), (79, 28), (100, 28), (52, 28), (59, 28), (222, 28), (103, 28), (36, 28), (178, 28), (101, 28), (69, 28), (61, 28), (37, 27), (212, 27), (419, 27), (82, 27), (47, 27), (186, 27), (131, 26),

==========================================================================================================================================================================================

## Top k channels
The case of a lot of channels are same as 0. So the front channels are selected.

So we select top k channels.

1. Comapring adversarial images' feature maps


In [39]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
device = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=100, shuffle=False, num_workers=4)

robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=device) # original model
attack1 = PGD(robust_model, cuda=device) # robust model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.to(device)
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(pgd_imgs)
    
    robust_holder = []
    
    def forwardhooking(m, inp, out):
        robust_holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)
    
    robust_model(pgd_imgs)
    
    # for name, 
    
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], robust_holder[0][:,:,-1])
    _, max_indcies = torch.topk(sim, 10, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()


    for i in range(batch_size):
        max_list.extend(max_indcies[i])
        min_list.extend(min_indcies[i])
    

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

print(len(min_dict_sorted),'\n' ,min_dict_sorted)
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

True
33 
 [(1, 9044), (9, 8310), (0, 8250), (2, 8061), (8, 7879), (7, 7763), (10, 7414), (4, 6911), (5, 6687), (6, 6559), (3, 5465), (11, 5303), (13, 3571), (12, 3161), (14, 1807), (15, 1094), (16, 932), (18, 531), (17, 476), (19, 244), (20, 226), (22, 103), (21, 94), (24, 27), (25, 27), (23, 26), (27, 14), (29, 9), (32, 4), (26, 3), (33, 3), (34, 1), (31, 1)]
512 
 [(220, 1695), (248, 1409), (3, 1367), (355, 1276), (87, 1118), (497, 1081), (255, 1003), (55, 974), (247, 973), (164, 969), (419, 920), (440, 853), (466, 842), (390, 802), (402, 792), (221, 742), (117, 733), (84, 732), (354, 701), (48, 689), (316, 670), (15, 632), (212, 620), (229, 611), (50, 596), (445, 582), (468, 582), (92, 581), (6, 578), (254, 555), (12, 526), (14, 519), (62, 517), (185, 509), (310, 509), (11, 495), (133, 489), (511, 484), (20, 482), (336, 449), (407, 429), (386, 418), (383, 417), (451, 414), (501, 411), (196, 408), (165, 401), (169, 393), (291, 389), (150, 389), (96, 389), (18, 381), (178, 376), (305,

## Comparing original images' feature maps and adversarial images' feature maps
### 1. Original model

In [42]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(ori_imgs)
    model(pgd_imgs)
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    _, max_indcies = torch.topk(sim, 10, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()

    for i in range(batch_size):
        max_list.extend(max_indcies[i])
        min_list.extend(min_indcies[i])

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

print(len(min_dict_sorted),'\n' ,min_dict_sorted)
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

True
349 
 [(9, 3385), (22, 3376), (0, 3335), (1, 3269), (6, 3177), (10, 3035), (7, 3002), (18, 2837), (2, 2786), (16, 2651), (20, 2587), (8, 2569), (17, 2553), (11, 2478), (13, 2468), (3, 2458), (12, 2439), (14, 2230), (19, 2184), (31, 2177), (5, 2081), (15, 2065), (21, 2060), (25, 1915), (27, 1847), (24, 1843), (33, 1752), (26, 1724), (23, 1718), (4, 1682), (43, 1635), (35, 1303), (32, 1148), (42, 1125), (28, 1076), (30, 1027), (36, 943), (29, 854), (46, 827), (54, 797), (34, 700), (38, 689), (44, 676), (37, 672), (39, 653), (45, 632), (40, 537), (53, 444), (41, 433), (51, 342), (61, 326), (47, 309), (56, 307), (73, 306), (50, 295), (67, 283), (68, 262), (52, 247), (49, 235), (58, 209), (48, 208), (91, 185), (59, 184), (65, 179), (85, 178), (60, 171), (69, 159), (77, 152), (145, 150), (64, 141), (86, 139), (72, 136), (124, 130), (108, 127), (84, 126), (81, 124), (76, 115), (95, 113), (79, 110), (55, 110), (96, 109), (142, 105), (57, 103), (97, 102), (63, 97), (110, 94), (104, 93), (6

### 2. Robust model

In [43]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(cuda)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()


attack = PGD(robust_model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []


for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    robust_model(ori_imgs)
    robust_model(pgd_imgs)
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    _, max_indcies = torch.topk(sim, 10, dim=1)
    max_indcies = max_indcies.squeeze(0).tolist()
    _, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_indcies = min_indcies.squeeze(0).tolist()
    # max_ind = torch.argmax(sim).data.item()
    # min_ind = torch.argmin(sim).data.item()

    for i in range(batch_size):
        max_list.extend(max_indcies[i])
        min_list.extend(min_indcies[i])

max_dict = {}
min_dict = {}
for i, j in zip(max_list, min_list):
    if i in max_dict:
        max_dict[i] += 1
    else:
        max_dict[i] = 1
        
    if j in min_dict:
        min_dict[j] += 1
    else:
        min_dict[j] = 1


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

print(len(min_dict_sorted),'\n' ,min_dict_sorted)
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

True
50 
 [(1, 7597), (10, 6402), (2, 6015), (7, 5923), (0, 5906), (13, 5893), (11, 5801), (9, 5671), (4, 5611), (8, 5562), (5, 5252), (16, 3855), (14, 3752), (17, 3066), (6, 2953), (12, 2682), (3, 2603), (18, 2287), (19, 2108), (22, 1857), (15, 1757), (21, 1311), (20, 1219), (25, 1131), (23, 1066), (27, 793), (24, 610), (29, 274), (26, 255), (32, 167), (33, 110), (28, 99), (35, 79), (34, 64), (31, 61), (37, 61), (30, 53), (36, 25), (40, 24), (39, 17), (42, 9), (45, 5), (38, 4), (46, 2), (41, 2), (53, 2), (43, 1), (44, 1), (54, 1), (47, 1)]
511 
 [(20, 1347), (43, 1321), (55, 1303), (15, 1271), (3, 1201), (12, 1123), (68, 1121), (6, 1114), (84, 1082), (78, 1059), (62, 1041), (24, 990), (30, 984), (35, 959), (50, 953), (87, 923), (51, 920), (18, 917), (56, 891), (97, 867), (29, 837), (48, 797), (14, 792), (117, 785), (28, 783), (92, 750), (26, 737), (19, 736), (21, 734), (116, 703), (8, 697), (5, 672), (17, 653), (123, 649), (57, 646), (34, 646), (16, 640), (64, 629), (46, 626), (98, 62

==========================================================================================================================================================================================

# Check the value of similiarity of channels

Still the front indcies of channels are selected.

Another case: If the most channels are same as 0, we can check this phenemenon by checking channels' mean.

## Comparing original images' feature maps and adversarial images' feature maps

In [1]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
device = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=device) # original model
attack1 = PGD(robust_model, cuda=device) # robust model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []
max_dict = {}
min_dict = {}

for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.to(device)
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(pgd_imgs)
    
    robust_holder = []
    
    def forwardhooking(m, inp, out):
        robust_holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)
    
    robust_model(pgd_imgs)
    
    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], robust_holder[0][:,:,-1])
    max_values, max_indcies = torch.topk(sim, 10, dim=1)
    max_values = max_values.tolist()
    max_indcies = max_indcies.squeeze(0).tolist()
    min_values, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_values = min_values.tolist()
    min_indcies = min_indcies.squeeze(0).tolist()
    # for i, j in 

    for i in range(batch_size):
        for j in range(10):
            if max_indcies[i][j] in max_dict:
                max_dict[max_indcies[i][j]].append(max_values[i][j])
            else:
                max_dict[max_indcies[i][j]] = [max_values[i][j]]
                
            if min_indcies[i][j] in min_dict:
                min_dict[min_indcies[i][j]].append(min_values[i][j]) # Append minimum value to minimun index so dict will {1:0.65} etc.
            else:
                min_dict[min_indcies[i][j]] = [min_values[i][j]]
    


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=True)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


In [3]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

33 
 [(1, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

The whole minimum values are 0 -> similarity is 0

Two models don't map the perturbed images and original images into same feature map -> almost different feature maps

In [12]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

512 
 [(421, [1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9815219640731812, 1.0, 0.9850131273269653, 1.0, 0.9928151965141296, 0.9764176607131958, 0.9895732998847961, 1.0, 1.0, 0.9658449292182922, 0.9966259598731995, 0.9636701345443726, 0.998413622379303, 1.0, 0.9974603652954102, 1.0, 1.0, 0.9914820194244385, 0.9875385761260986, 1.0, 1.0, 1.0]), (273, [1.0, 1.0, 1.0, 1.0, 1.0, 0.9996913075447083, 0.978743314743042, 1.0, 0.970564603805542, 0.9981582164764404, 1.0, 0.9822498559951782, 1.0, 1.0, 0.977729082107544, 0.9777551889419556, 0.9721896648406982, 0.9786397218704224, 0.9791186451911926, 0.997678279876709, 0.9847639799118042, 0.9827722311019897, 0.9583057165145874, 1.0, 1.0, 1.0, 0.9908761978149414, 0.9966937899589539, 0.9724483489990234, 0.9750752449035645, 1.0, 0.9777262210845947, 0.9998306632041931, 0.9971644282341003, 0.9704693555831909, 0.9793955683708191, 0.9853464365005493, 0.993628203868866, 0.9907703399658203, 0.9792793989181519, 0.9851414561271667, 0.9999901056289673, 0.997596

original model
pgd img & original img

In [20]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


attack = PGD(model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_list = []
robust_max_list = []
min_list = []
robust_min_list = []
max_dict = {}
min_dict = {}

for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    model(ori_imgs)
    model(pgd_imgs)
    

    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    max_values, max_indcies = torch.topk(sim, 10, dim=1)
    max_values = max_values.tolist()
    max_indcies = max_indcies.squeeze(0).tolist()
    min_values, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_values = min_values.tolist()
    min_indcies = min_indcies.squeeze(0).tolist()

    for i in range(batch_size):
        for j in range(10):
            if max_indcies[i][j] in max_dict:
                max_dict[max_indcies[i][j]].append(max_values[i][j])
            else:
                max_dict[max_indcies[i][j]] = [max_values[i][j]]
                
            if min_indcies[i][j] in min_dict:
                min_dict[min_indcies[i][j]].append(min_values[i][j])
            else:
                min_dict[min_indcies[i][j]] = [min_values[i][j]]
    


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=False)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


In [21]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

349 
 [(261, [0.0]), (273, [0.0]), (275, [0.0]), (219, [0.0]), (223, [0.0]), (511, [0.0]), (439, [0.0]), (277, [0.0]), (304, [0.0]), (249, [0.0]), (239, [0.0]), (220, [0.0]), (297, [0.0]), (169, [0.0]), (368, [0.0]), (438, [0.0]), (400, [0.0]), (393, [0.0]), (496, [0.0]), (298, [0.0]), (506, [0.0]), (503, [0.0]), (477, [0.0]), (269, [0.0]), (217, [0.0]), (299, [0.0]), (191, [0.0]), (173, [0.0]), (345, [0.0]), (318, [0.0]), (405, [0.0]), (433, [0.0]), (350, [0.0]), (421, [0.0]), (200, [0.0]), (300, [0.0]), (385, [0.0]), (403, [0.0]), (471, [0.0]), (328, [0.0]), (307, [0.0]), (323, [0.0]), (446, [0.0]), (388, [0.0]), (158, [0.0, 0.0]), (398, [0.0, 0.0]), (464, [0.0, 0.0]), (201, [0.0, 0.0]), (250, [0.0, 0.0]), (336, [0.0, 0.0]), (263, [0.0, 0.0]), (361, [0.0, 0.0]), (410, [0.0, 0.0]), (310, [0.0, 0.0]), (210, [0.0, 0.0]), (238, [0.0, 0.0]), (486, [0.0, 0.0]), (211, [0.0, 0.0]), (380, [0.0, 0.0]), (237, [0.0, 0.0]), (294, [0.0, 0.0]), (295, [0.0, 0.0]), (163, [0.0, 0.0]), (259, [0.0, 0.0]

In [22]:
min_dict_sorted

[(261, [0.0]),
 (273, [0.0]),
 (275, [0.0]),
 (219, [0.0]),
 (223, [0.0]),
 (511, [0.0]),
 (439, [0.0]),
 (277, [0.0]),
 (304, [0.0]),
 (249, [0.0]),
 (239, [0.0]),
 (220, [0.0]),
 (297, [0.0]),
 (169, [0.0]),
 (368, [0.0]),
 (438, [0.0]),
 (400, [0.0]),
 (393, [0.0]),
 (496, [0.0]),
 (298, [0.0]),
 (506, [0.0]),
 (503, [0.0]),
 (477, [0.0]),
 (269, [0.0]),
 (217, [0.0]),
 (299, [0.0]),
 (191, [0.0]),
 (173, [0.0]),
 (345, [0.0]),
 (318, [0.0]),
 (405, [0.0]),
 (433, [0.0]),
 (350, [0.0]),
 (421, [0.0]),
 (200, [0.0]),
 (300, [0.0]),
 (385, [0.0]),
 (403, [0.0]),
 (471, [0.0]),
 (328, [0.0]),
 (307, [0.0]),
 (323, [0.0]),
 (446, [0.0]),
 (388, [0.0]),
 (158, [0.0, 0.0]),
 (398, [0.0, 0.0]),
 (464, [0.0, 0.0]),
 (201, [0.0, 0.0]),
 (250, [0.0, 0.0]),
 (336, [0.0, 0.0]),
 (263, [0.0, 0.0]),
 (361, [0.0, 0.0]),
 (410, [0.0, 0.0]),
 (310, [0.0, 0.0]),
 (210, [0.0, 0.0]),
 (238, [0.0, 0.0]),
 (486, [0.0, 0.0]),
 (211, [0.0, 0.0]),
 (380, [0.0, 0.0]),
 (237, [0.0, 0.0]),
 (294, [0.0, 0.0]),


In [23]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

512 
 [(382, [1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.0000003576278687, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.00000023841857

Robust model

Comapring feature map of original images and perturbed images

In [24]:
import torch
import torchvision.models as models
import torch.nn as nn
import torchvision.transforms as transforms
from pytorch_grad_cam.utils.image import show_cam_on_image
from torchvision.models import resnet50
from PGD import PGD
from my_resnet import *
from models import *
import os
import torchvision

os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"  # Arrange GPU devices starting from 0
os.environ["CUDA_VISIBLE_DEVICES"]= "1,2"  # Set the GPUs 2 and 3 to use
    
cuda = True if torch.cuda.is_available() else False
print(device)

transform_test = transforms.Compose([
    transforms.ToTensor(),
])

batch_size = 100

test_dataset = torchvision.datasets.CIFAR10(root='/workspace/my_data', train=False, download=False, transform=transform_test)

test_loader = torch.utils.data.DataLoader(test_dataset, batch_size=batch_size, shuffle=False, num_workers=4)

model = ResNet18() ## original model
checkpoint_path2 = '/workspace/checkpoint/resnet18_cifar10'
checkpoint2 = torch.load(checkpoint_path2)['net']
for key in list(checkpoint2.keys()):
    checkpoint2[key.replace('module.', '')] = checkpoint2.pop(key)
model.load_state_dict(checkpoint2, strict=False)## original model
model = model.cuda()
model.eval()


robust_model = ResNet18()
checkpoint_path1 = '/workspace/checkpoint/pgd_adversarial_training'
checkpoint1 = torch.load(checkpoint_path1)['net']
for key in list(checkpoint1.keys()):
    checkpoint1[key.replace('module.', '')] = checkpoint1.pop(key)
robust_model.load_state_dict(checkpoint1, strict=False)
robust_model = robust_model.cuda()
robust_model.eval()

attack = PGD(model, cuda=cuda) # original model

cos = nn.CosineSimilarity(dim=2)

max_dict = {}
min_dict = {}

for ori_imgs, ori_labels in test_loader:

    pgd_imgs = attack(ori_imgs, ori_labels)
    ori_imgs = ori_imgs.cuda()
    # robust_pgd_imgs = attack1(ori_imgs, ori_labels)
    # pgd_input_tensor = attack(ori_imgs, ori_labels)
    # Note: input_tensor can be a batch tensor with several images!

    holder = []
            
    def forwardhooking(m, inp, out):
        holder.append(out)
    # forwardhooking = ForwardHooking

    for name, m in robust_model.named_modules():
        if name == 'layer4.1':
            m.register_forward_hook(forwardhooking)

    robust_model(ori_imgs)
    robust_model(pgd_imgs)
    

    # get cosine similarity along 512channel in last layer
    sim = cos(holder[0][:,:,-1], holder[1][:,:,-1])
    max_values, max_indcies = torch.topk(sim, 10, dim=1)
    max_values = max_values.tolist()
    max_indcies = max_indcies.squeeze(0).tolist()
    min_values, min_indcies = torch.topk(sim, 10, dim=1, largest=False)
    min_values = min_values.tolist()
    min_indcies = min_indcies.squeeze(0).tolist()

    for i in range(batch_size):
        for j in range(10):
            if max_indcies[i][j] in max_dict:
                max_dict[max_indcies[i][j]].append(max_values[i][j])
            else:
                max_dict[max_indcies[i][j]] = [max_values[i][j]]
                
            if min_indcies[i][j] in min_dict:
                min_dict[min_indcies[i][j]].append(min_values[i][j])
            else:
                min_dict[min_indcies[i][j]] = [min_values[i][j]]
    


min_dict_sorted = sorted(min_dict.items(), key=lambda x: x[1], reverse=False)
max_dict_sorted = sorted(max_dict.items(), key=lambda x: x[1], reverse=True)
torch.cuda.empty_cache()

True


In [25]:
print(len(min_dict_sorted),'\n' ,min_dict_sorted)

50 
 [(43, [0.0]), (44, [0.0]), (54, [0.0]), (47, [0.0]), (46, [0.0, 0.0]), (41, [0.0, 0.0]), (53, [0.0, 0.0]), (38, [0.0, 0.0, 0.0, 0.0]), (45, [0.0, 0.0, 0.0, 0.0, 0.0]), (42, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]), (39, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]), (40, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]), (36, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]), (30, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]), (31, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0

In [27]:
min_dict_sorted

[(43, [0.0]),
 (44, [0.0]),
 (54, [0.0]),
 (47, [0.0]),
 (46, [0.0, 0.0]),
 (41, [0.0, 0.0]),
 (53, [0.0, 0.0]),
 (38, [0.0, 0.0, 0.0, 0.0]),
 (45, [0.0, 0.0, 0.0, 0.0, 0.0]),
 (42, [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]),
 (39,
  [0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0]),
 (40,
  [0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0]),
 (36,
  [0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0]),
 (30,
  [0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0

In [26]:
print(len(max_dict_sorted),'\n' ,max_dict_sorted)

511 
 [(504, [1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579, 1.000000238418579

Minimum values of similarity are almost 0. So the function select some channels that has value of 0. So the front channels are selected.

Not the front channels are problems

The number of channels with maximum similarity is various both original model and robust model. (512, 511) almost all channels are selected not specific channels.


However the number of the channels with minimum similarity is not that much various compared to maxium. (349, 50) -> 50 channels are selected in robust model.

==========================================================================================================================================================================================

# Conclusion

### 1. Comparing feature maps between normal model and robust model
##### A. Comparing adversarial images' feature maps(noraml model, robust model) using cosine similarity

with top 1 (biggest, smallest) similarity
> Channel of maximum values are vary but the number of channel with minimun values are small
>> But almost of channels has 0 similarity value -> That indices are not meaningful (trying to get top k(5 or 10) indices)
>>> Number of channels with maximum values: 512 -> whole channels are reported
>>> Number of channels with minimum values: 5 -> specific channels are reported. But not meaningful as referred above

##### B. Comparing original images' feature maps(normal model, robust model) using cosine similarity

Showing similar aspect with A

## Robust model's feature maps are more robust than normal model's feature maps
Compare original image's feature maps and adversarial image's feature maps

The number of channel with minimum values are smaller than normal model

We can infer that robust model's small number of channels are disupted by adversarial images than normal model